# pyGSTi Demo

In [1]:
#Please note you will, as of 11/19/21, need the master branch version of pyGSTi 
#in order to run the IBM portion of the demo (UnitaryFundDemoNotebook2)
#Repository is located at https://github.com/pyGSTio/pyGSTi.
#All other functionality should be supported via the PyPI version of pyGSTi (https://pypi.org/project/pyGSTi/)
import pygsti
import time

In [2]:
from pygsti.modelpacks import smq1Q_XYI

# pyGSTi as a standalone QCVV tool

# Examples 1:  GST report

## Create experiment design

In [3]:
exp_design = smq1Q_XYI.create_gst_experiment_design(max_max_length=32)  

## Write an empty protocol data object (create a template to fill in)

In [4]:
#If not already present, first make a folder called "tuorial_files" to results output, e.g:
#import os
#os.mkdir('tutorial_files')

pygsti.io.write_empty_protocol_data('tutorial_files/test_gst_dir', exp_design, clobber_ok=True)
#Actual (empty) dataset located at tutorial_files/test_gst_dir/data/dataset.txt

## Fill in the template with simulated data (you would run the experiment and use actual data)

In [5]:
noisy_model_1 = smq1Q_XYI.target_model().depolarize(op_noise=0.01, spam_noise=0.001)

pygsti.io.fill_in_empty_dataset_with_fake_data(
    "tutorial_files/test_gst_dir/data/dataset.txt",
    noisy_model_1,
    num_samples=1000, seed=1234)

## Load the protocol data object

In [6]:
data = pygsti.io.read_data_from_dir('tutorial_files/test_gst_dir')

## Run GST on the data!
### (Should take ~30 s)

In [7]:
gst_protocol = pygsti.protocols.StandardGST()
results = gst_protocol.run(data)

-- Std Practice:  Iter 1 of 3  (full TP) --: 
  --- Iterative GST: [##################################################] 100.0%  784 circuits ---
  Iterative GST Total Time: 2.7s
-- Std Practice:  Iter 2 of 3  (CPTP) --: 


  --- Iterative GST: [##################################################] 100.0%  784 circuits ---
  Iterative GST Total Time: 28.6s
-- Std Practice:  Iter 3 of 3  (Target) --: 


## Create GST report
### (Should take ~30 s)

In [8]:
report = pygsti.report.construct_standard_report(
    results, title="GST Overview Tutorial Example Report")

Running idle tomography
Computing switchable properties
Found standard clifford compilation from smq1Q_XYI
Found standard clifford compilation from smq1Q_XYI
Found standard clifford compilation from smq1Q_XYI


In [9]:
report.write_html("tutorial_files/ExampleReport")

# Example 2 - Randomized Benchmarking (Clifford)

## Create a workspace

In [10]:
ws = pygsti.report.Workspace()
ws.init_notebook_mode(autodisplay=True)

## Create a processor specification (QubitProcessorSpec)

In [11]:
qubit_labels = [0]
gate_names = ['Gxpi2', 'Gxmpi2', 'Gypi2', 'Gympi2']
pspec = pygsti.processors.QubitProcessorSpec(len(qubit_labels), gate_names,
                 qubit_labels=qubit_labels)


## Create experiment design

In [12]:
# define the quantum processor (or piece of a processor) we'll be doing RB on
depths = [0, 10, 20, 30]
circuits_per_depth = 50

# Create compilation rules from native gates to Cliffords
from pygsti.processors import CliffordCompilationRules as CCR
compilations = {'absolute': CCR.create_standard(pspec, 'absolute', ('paulis', '1Qcliffords'), verbosity=0),            
                'paulieq': CCR.create_standard(pspec, 'paulieq', ('1Qcliffords', 'allcnots'), verbosity=0)}

# create an experiment design
exp_design = pygsti.protocols.CliffordRBDesign(pspec, compilations, depths, circuits_per_depth)
#Should take < 30s

- Sampling 50 circuits at CRB length 0 (1 of 4 depths) with seed 752524
- Sampling 50 circuits at CRB length 10 (2 of 4 depths) with seed 752574
- Sampling 50 circuits at CRB length 20 (3 of 4 depths) with seed 752624
- Sampling 50 circuits at CRB length 30 (4 of 4 depths) with seed 752674


## Write an empty data object (create a template to fill in)

In [13]:
# write an empty data object (creates a template to fill in)
pygsti.io.write_empty_protocol_data('tutorial_files/test_rb_dir', exp_design, clobber_ok=True)

## Fill in the template with simulated data (you would run the experiment and use actual data)

In [14]:
# Use a model with 1% depolarization on all gates
mdl_2 = pygsti.models.create_crosstalk_free_model(pspec, depolarization_strengths={
    'Gxpi2': 0.01, 'Gxmpi2': 0.01, 'Gypi2': 0.01, 'Gympi2': 0.01}, simulator="map")
pygsti.io.fill_in_empty_dataset_with_fake_data(
    "tutorial_files/test_rb_dir/data/dataset.txt", mdl_2, num_samples=1000, seed=1234)

## Load the data object

In [15]:
# load the data object back in, now with the experimental data
data = pygsti.io.read_data_from_dir('tutorial_files/test_rb_dir')

## Run RB analysis on data!

In [16]:
rb_proto = pygsti.protocols.RB()
rbresults = rb_proto.run(data)
#Should take ~5 s.

## Look at results

In [17]:
#Create a RB plot
ws.RandomizedBenchmarkingPlot(rbresults)

# Example 3:  GST with "ingredient" objects within a workflow

## Do GST on $\{H, T\}$ gate set
### Define $\{H, T\}$ gate set

In [18]:
import scipy
import numpy as np

In [19]:
qubit_labels = [0]
gate_names = ['Gh','Gt']
Ut = scipy.linalg.expm((-1j *  np.pi/4 * pygsti.sigmaz)/2)
pspec = pygsti.processors.QubitProcessorSpec(len(qubit_labels), gate_names,
                 qubit_labels=qubit_labels,
                 nonstd_gate_unitaries = {'Gt':Ut})

target_model_HT = pygsti.models.create_explicit_model(pspec,ideal_gate_type='full',ideal_spam_type='full')

### Oh, what if we want to add another gate?  Say, $T^\dagger$?

In [20]:
Utdag = scipy.linalg.expm((1j *  np.pi/4 * pygsti.sigmaz)/2)
target_model_HT['Gtdag',0] = pygsti.unitary_to_pauligate(Utdag)

In [21]:
print(target_model_HT)

rho0 = FullState with dimension 4
 0.71   0   0 0.71


Mdefault = UnconstrainedPOVM with effect vectors:
0: FullPOVMEffect with dimension 4
 0.71   0   0 0.71

1: FullPOVMEffect with dimension 4
 0.71   0   0-0.71



Gh:0 = 
FullArbitraryOp with shape (4, 4)
 1.00   0   0   0
   0   0   0 1.00
   0   0-1.00   0
   0 1.00   0   0


Gt:0 = 
FullArbitraryOp with shape (4, 4)
 1.00   0   0   0
   0 0.71-0.71   0
   0 0.71 0.71   0
   0   0   0 1.00


Gtdag:0 = 
FullArbitraryOp with shape (4, 4)
 1.00   0   0   0
   0 0.71 0.71   0
   0-0.71 0.71   0
   0   0   0 1.00






In [22]:
Gtdag = target_model_HT['Gtdag',0]
print(Gtdag)

FullArbitraryOp with shape (4, 4)
 1.00   0   0   0
   0 0.71 0.71   0
   0-0.71 0.71   0
   0   0   0 1.00



In [23]:
Gt = target_model_HT['Gt',0]
print(Gtdag.dot(Gt))

[[ 1.00000000e+00  0.00000000e+00  0.00000000e+00  2.02930727e-17]
 [ 0.00000000e+00  1.00000000e+00 -4.26642159e-17  0.00000000e+00]
 [ 0.00000000e+00 -4.26642159e-17  1.00000000e+00  0.00000000e+00]
 [ 2.02930727e-17  0.00000000e+00  0.00000000e+00  1.00000000e+00]]


## Create custom fiducials, germs

In [24]:
prep_fiducials, meas_fiducials = pygsti.algorithms.fiducialselection.find_fiducials(target_model_HT,
                                                                                    max_fid_length=3)
#Should take <5 s

Using GRASP algorithm.
Preparation fiducials:
['{}', 'Gh:0@(0)', 'Gh:0Gt:0Gt:0@(0)', 'Gh:0Gtdag:0Gtdag:0@(0)']
Score: 31.999999999999982
Measurement fiducials:
['{}', 'Gt:0Gh:0@(0)', 'Gtdag:0Gh:0@(0)']
Score: 9.999999999999996


In [25]:
start = time.time()
germs = pygsti.algorithms.germselection.find_germs(target_model_HT,randomize=False)
end = time.time()
#Should take <5 s

Using greedy algorithm.
Constructed germ set:
['Gh:0@(0)', 'Gt:0@(0)', 'Gtdag:0@(0)', 'Gt:0Gtdag:0@(0)', 'Gh:0Gtdag:0Gtdag:0Gtdag:0@(0)']
Score: Score: major=-34.0 minor=68.48518790283792, N: 34


In [26]:
#Minor bug that needs to be fixed.
prep_fiducials[0] = pygsti.circuits.Circuit([],line_labels=(0,))
meas_fiducials[0] = pygsti.circuits.Circuit([],line_labels=(0,))

In [27]:
#Write prep and measurement fiducials, germs to files
pygsti.io.write_circuit_list('HTTdag_preps.txt',prep_fiducials)
pygsti.io.write_circuit_list('HTTdag_effects.txt',meas_fiducials)
pygsti.io.write_circuit_list('HTTdag_germs.txt',germs)

In [28]:
#Could run lines below to skip having to regenerate the circuit lists:
#prep_fiducials = pygsti.io.load_circuit_list('HTTdag_preps.txt')
#meas_fiducials = pygsti.io.load_circuit_list('HTTdag_effects.txt')
#germs = pygsti.io.load_circuit_list('HTTdag_germs.txt')

## Create experiment design

In [29]:
max_lengths = [1,2,4,8,16,32]
exp_design_HT = pygsti.protocols.StandardGSTDesign(target_model_HT,prep_fiducials,meas_fiducials,
                                                   germs,max_lengths)

## Let's look at the circuits in the experiment design

In [30]:
circuits = list(exp_design_HT.all_circuits_needing_data)
circuits

[Circuit({}@(0)),
 Circuit(Gt:0Gh:0@(0)),
 Circuit(Gtdag:0Gh:0@(0)),
 Circuit(Gh:0@(0)),
 Circuit(Gh:0Gt:0Gt:0@(0)),
 Circuit(Gh:0Gtdag:0Gtdag:0@(0)),
 Circuit(Gh:0Gt:0Gh:0@(0)),
 Circuit(Gh:0Gtdag:0Gh:0@(0)),
 Circuit(Gh:0Gt:0Gt:0Gt:0Gh:0@(0)),
 Circuit(Gh:0Gt:0Gt:0Gtdag:0Gh:0@(0)),
 Circuit(Gh:0Gtdag:0Gtdag:0Gt:0Gh:0@(0)),
 Circuit(Gh:0Gtdag:0Gtdag:0Gtdag:0Gh:0@(0)),
 Circuit(Gh:0(Gh:0)@(0)),
 Circuit(Gh:0(Gh:0)Gt:0Gh:0@(0)),
 Circuit(Gh:0(Gh:0)Gtdag:0Gh:0@(0)),
 Circuit(Gh:0Gt:0Gt:0(Gh:0)@(0)),
 Circuit(Gh:0Gt:0Gt:0(Gh:0)Gt:0Gh:0@(0)),
 Circuit(Gh:0Gt:0Gt:0(Gh:0)Gtdag:0Gh:0@(0)),
 Circuit(Gh:0Gtdag:0Gtdag:0(Gh:0)@(0)),
 Circuit(Gh:0Gtdag:0Gtdag:0(Gh:0)Gt:0Gh:0@(0)),
 Circuit(Gh:0Gtdag:0Gtdag:0(Gh:0)Gtdag:0Gh:0@(0)),
 Circuit((Gt:0)@(0)),
 Circuit((Gt:0)Gt:0Gh:0@(0)),
 Circuit((Gt:0)Gtdag:0Gh:0@(0)),
 Circuit(Gh:0(Gt:0)@(0)),
 Circuit(Gh:0(Gt:0)Gtdag:0Gh:0@(0)),
 Circuit(Gh:0Gt:0Gt:0(Gt:0)@(0)),
 Circuit(Gh:0Gt:0Gt:0(Gt:0)Gt:0Gh:0@(0)),
 Circuit(Gh:0Gt:0Gt:0(Gt:0)Gtdag:0Gh:0@(0)),
 C

In [31]:
circ_1 = circuits[1]
circ_16= circuits[16]

In [32]:
circ_1

Circuit(Gt:0Gh:0@(0))

In [33]:
print(circ_1)

Qubit 0 ---|Gt|-|Gh|---



In [34]:
print(circ_16)

Qubit 0 ---|Gh|-|Gt|-|Gt|-|Gh|-|Gt|-|Gh|---



In [35]:
target_model_HT.probabilities(circ_1)

OutcomeLabelDict([(('0',), 0.5), (('1',), 0.5)])

In [36]:
target_model_HT.probabilities(circ_16)

OutcomeLabelDict([(('0',), 0.8535533905932737), (('1',), 0.1464466094067261)])

## Let's make a noisy model to simulate data on

In [37]:
noisy_model_HT = target_model_HT.copy()

In [38]:
noisy_model_HT['Gt'] = pygsti.unitary_to_pauligate(scipy.linalg.expm(-1j * pygsti.sigmaz * (np.pi/4 + 1e-2))/2)
noisy_model_HT['Gtdag'] = pygsti.unitary_to_pauligate(scipy.linalg.expm(1j * pygsti.sigmaz * (np.pi/4 + 1e-2))/2)
#noisy_model_HT = noisy_model_HT.depolarize(op_noise=1e-3,spam_noise=1e-2)
noisy_model_HT = noisy_model_HT.depolarize(op_noise=1e-3)

## Let's simulate the dataset

In [39]:
pygsti.io.write_empty_protocol_data('tutorial_files/test_gst_dir_ht', exp_design_HT, clobber_ok=True)

In [40]:
dataset_ht = pygsti.data.simulate_data(noisy_model_HT,exp_design_HT,1000)
#Could also pass circuit list directly:
#dataset_ht = pygsti.data.simulate_data(noisy_model_HT,circuits,1000)

In [41]:
pygsti.io.write_dataset('tutorial_files/test_gst_dir_ht/data/dataset.txt',dataset_ht)

In [42]:
data_ht = pygsti.io.read_data_from_dir('tutorial_files/test_gst_dir_ht')

## Run GST on data

In [43]:
results_ht = pygsti.protocols.StandardGST().run(data_ht)

-- Std Practice:  Iter 1 of 3  (full TP) --: 
  --- Iterative GST: [##################################################] 100.0%  313 circuits ---
  Iterative GST Total Time: 1.6s
-- Std Practice:  Iter 2 of 3  (CPTP) --: 
  --- Iterative GST: [##################################################] 100.0%  313 circuits ---
  Iterative GST Total Time: 13.8s
-- Std Practice:  Iter 3 of 3  (Target) --: 


In [44]:
report_ht = pygsti.report.construct_standard_report(
    results_ht, title="GST H T Tdagger report")
report_ht.write_html("tutorial_files/HT_Report")

Running idle tomography
Computing switchable properties


# Do things with the results!

In [45]:
print(results_ht)

----------------------------------------------------------
----------- pyGSTi ModelEstimateResults Object -----------
----------------------------------------------------------

How to access my contents:

 .dataset    -- the DataSet used to generate these results

 .circuit_lists   -- a dict of Circuit lists w/keys:
 ---------------------------------------------------------
  iteration
  prep fiducials
  meas fiducials
  germs
  final

 .estimates   -- a dictionary of Estimate objects:
 ---------------------------------------------------------
  full TP
  CPTP
  Target




In [46]:
cptp_estimate = results_ht.estimates['CPTP']

print(cptp_estimate)

----------------------------------------------------------
---------------- pyGSTi Estimate Object ------------------
----------------------------------------------------------

How to access my contents:

 .models   -- a dictionary of Model objects w/keys:
 ---------------------------------------------------------
  target
  seed
  iteration 0 estimate
  iteration 1 estimate
  iteration 2 estimate
  iteration 3 estimate
  iteration 4 estimate
  iteration 5 estimate
  final iteration estimate
  stdgaugeopt

 .goparameters   -- a dictionary of gauge-optimization parameter dictionaries:
 ---------------------------------------------------------
  stdgaugeopt




In [47]:
#Print the final, gauge-optimized (to target) GST estimate (CPTP)

cptp_estimate_final_model = cptp_estimate.models['stdgaugeopt']

print(cptp_estimate_final_model)

rho0 = <pygsti.modelmembers.states.composedstate.ComposedState object at 0x7fc408101a90>

Mdefault = Lindblad-parameterized POVM of length 2


Gh:0 = 
Composed operation of 2 factors:
Factor 0:
StaticUnitaryOp with shape (2, 2)
 0.71 0.71
 0.71-0.71
Factor 1:
Exponentiated operation map with dim = 4, num params = 12


Gt:0 = 
Composed operation of 2 factors:
Factor 0:
StaticUnitaryOp with shape (2, 2)
 1.00  +0j   0  +0j
   0  +0j 0.71+0.71j
Factor 1:
Exponentiated operation map with dim = 4, num params = 12


Gtdag:0 = 
Composed operation of 2 factors:
Factor 0:
StaticUnitaryOp with shape (2, 2)
 1.00  +0j   0  +0j
   0  +0j 0.71-0.71j
Factor 1:
Exponentiated operation map with dim = 4, num params = 12






In [48]:
#Look at gate matrix directly
print(results_ht.estimates['CPTP'].models['stdgaugeopt']['Gh',0].to_dense())

[[ 1.00000000e+00  3.21203142e-16 -1.24254945e-18  7.16543176e-17]
 [ 2.27395176e-04 -3.78948856e-04  1.41639677e-04  9.99553515e-01]
 [ 7.74525009e-04  1.04855738e-04 -9.98808421e-01  2.23150492e-05]
 [-1.03194514e-03  9.98721152e-01 -2.68836422e-04  7.34793390e-04]]


In [49]:
#Multiply gate matrices
np.dot(results_ht.estimates['CPTP'].models['stdgaugeopt']['Gh',0].to_dense(),
       results_ht.estimates['CPTP'].models['stdgaugeopt']['Gh',0].to_dense())

array([[ 1.00000000e+00,  3.92643975e-16,  2.47512228e-20,
         3.92766670e-16],
       [-8.04065687e-04,  9.98275396e-01, -4.10240967e-04,
         3.55688815e-04],
       [ 9.23723636e-07, -8.24840173e-05,  9.97618270e-01,
         8.25368592e-05],
       [-8.05807258e-04,  3.55361274e-04,  4.09777084e-04,
         9.98275772e-01]])

In [50]:
#Look at error rates/coefficients
results_ht.estimates['CPTP'].models['stdgaugeopt']['Gh',0].errorgen_coefficients()

OrderedDict([(('H', ('X',), (0,)), -0.0004198976316330371),
             (('H', ('Y',), (0,)), -0.00267933145516025),
             (('H', ('Z',), (0,)), 0.0005837330861986813),
             (('S', ('X', 'X'), (0,)), (0.0005065235795067391+0j)),
             (('S', ('X', 'Y'), (0,)),
              (-2.986914078546029e-05-0.0002582099591395862j)),
             (('S', ('X', 'Z'), (0,)),
              (8.861300163683058e-05-0.00019381018196195946j)),
             (('S', ('Y', 'X'), (0,)),
              (-2.986914078546029e-05+0.0002582099591395862j)),
             (('S', ('Y', 'Y'), (0,)), (0.00013338875288324478+0j)),
             (('S', ('Y', 'Z'), (0,)),
              (9.357298827483468e-05+5.660092502680241e-05j)),
             (('S', ('Z', 'X'), (0,)),
              (8.861300163683058e-05+0.00019381018196195946j)),
             (('S', ('Z', 'Y'), (0,)),
              (9.357298827483468e-05-5.660092502680241e-05j)),
             (('S', ('Z', 'Z'), (0,)), (8.965949980146732e-05+0j))])

## Gauge-optimize to true gate set

In [51]:
gst_model_ht_gopt = pygsti.gaugeopt_to_target(results_ht.estimates['CPTP'].models['stdgaugeopt'],
                                             noisy_model_HT,item_weights={'spam':1e-2,'gates':1})

## Compute diamond distance between GST estimate and truth

In [52]:
pygsti.diamonddist(gst_model_ht_gopt['Gt',0].to_dense(),
                   noisy_model_HT['Gt',0].to_dense())

0.0019867866002027373

# Example 4:  Custom gate object

### Define a custom gate class:
$X(\pi/2)$ gate with only 2 parameters:  Over-rotation and depolarization.

In [53]:
class MyXPi2Operator(pygsti.modelmembers.operations.DenseOperator):
    def __init__(self):
        #initialize with no noise
        super(MyXPi2Operator,self).__init__(np.identity(4,'d'), "densitymx") # this is *super*-operator, so "densitymx"
        self.from_vector([0,0]) 
    
    @property
    def num_params(self): 
        return 2 # we have two parameters
    
    def to_vector(self):
        return np.array([self.depol_amt, self.over_rotation],'d') #our parameter vector
        
    def from_vector(self, v, close=False, dirty_value=True):
        #initialize from parameter vector v
        self.depol_amt = v[0]
        self.over_rotation = v[1]
        
        theta = (np.pi/2 + self.over_rotation)/2
        a = 1.0-self.depol_amt
        b = a*2*np.cos(theta)*np.sin(theta)
        c = a*(np.sin(theta)**2 - np.cos(theta)**2)
        
        # ._ptr is a member of DenseOperator and is a numpy array that is 
        # the dense Pauli transfer matrix of this operator
        # Technical note: use [:,:] instead of direct assignment so id of self._ptr doesn't change
        self._ptr[:,:] = np.array([[1,   0,   0,   0],
                                  [0,   a,   0,   0],
                                  [0,   0,   c,  -b],
                                  [0,   0,   b,   c]],'d')
        self.dirty = dirty_value  # mark that parameter vector may have changed
        
    def transform(self, S):
        # Update self with inverse(S) * self * S (used in gauge optimization)
        raise NotImplementedError("MyXPi2Operator cannot be transformed!")

## Make target model with custom gate class

In [54]:
customX_target_model = smq1Q_XYI.target_model()
customX_target_model.operations[('Gxpi2',0)] = MyXPi2Operator()

## Make experiment design

In [55]:
max_lengths = [1,2,4,8,16,32]
exp_design_customX = pygsti.protocols.StandardGSTDesign(customX_target_model,
                                                        smq1Q_XYI.prep_fiducials(),
                                                        smq1Q_XYI.meas_fiducials(),
                                                        smq1Q_XYI.germs(),
                                                        max_lengths)

In [56]:
pygsti.io.write_empty_protocol_data('tutorial_files/test_gst_dir_customX', exp_design_customX, clobber_ok=True)

## Make noisy custom model

In [57]:
customX_noisy_model = customX_target_model.copy()

In [58]:
#Set 5e-2 depolarization, 1e-1 over-rotation
customX_noisy_model['Gxpi2',0].from_vector([0.05,0.1])

## Generate data

In [59]:
dataset_customX = pygsti.data.simulate_data(customX_noisy_model,exp_design_customX,1000)
pygsti.io.write_dataset('tutorial_files/test_gst_dir_customX/data/dataset.txt',dataset_customX)

In [60]:
data_customX = pygsti.io.read_data_from_dir('tutorial_files/test_gst_dir_customX')

## Make custom GST protocol

In [61]:
customX_GST_protocol = pygsti.protocols.GateSetTomography(initial_model=customX_target_model,
                                                          gaugeopt_suite=None)

## Run custom GST protocol on data

In [62]:
results_customX = customX_GST_protocol.run(data_customX)

--- Iterative GST: Iter 1 of 6  92 circuits ---: 
  MatrixLayout: 1 processors divided into 1 x 1 (= 1) grid along circuit and parameter directions.
     1 atoms, parameter block size limits (None,)
  *** Distributing 1 atoms to 1 atom-processing groups (1 cores) ***
      More atom-processors than hosts: each host gets ~1 atom-processors
      Atom-processors already occupy a single node, dividing atom-processor into 1 param-processors.
  *** Divided 1-host atom-processor (~1 procs) into 1 param-processing groups ***
  --- chi2 GST ---
  Sum of Chi^2 = 42.3455 (92 data params - 46 (approx) model params = expected mean of 46; p-value = 0.626102)
  Completed in 0.3s
  Iteration 1 took 0.3s
  
--- Iterative GST: Iter 2 of 6  168 circuits ---: 
  MatrixLayout: 1 processors divided into 1 x 1 (= 1) grid along circuit and parameter directions.
     1 atoms, parameter block size limits (None,)
  *** Distributing 1 atoms to 1 atom-processing groups (1 cores) ***
      More atom-processors tha

## Look at results

In [63]:
print(results_customX)

----------------------------------------------------------
----------- pyGSTi ModelEstimateResults Object -----------
----------------------------------------------------------

How to access my contents:

 .dataset    -- the DataSet used to generate these results

 .circuit_lists   -- a dict of Circuit lists w/keys:
 ---------------------------------------------------------
  iteration
  prep fiducials
  meas fiducials
  germs
  final

 .estimates   -- a dictionary of Estimate objects:
 ---------------------------------------------------------
  GateSetTomography




In [64]:
custom_gst_estimate = results_customX.estimates['GateSetTomography']
print(custom_gst_estimate)

----------------------------------------------------------
---------------- pyGSTi Estimate Object ------------------
----------------------------------------------------------

How to access my contents:

 .models   -- a dictionary of Model objects w/keys:
 ---------------------------------------------------------
  seed
  iteration 0 estimate
  iteration 1 estimate
  iteration 2 estimate
  iteration 3 estimate
  iteration 4 estimate
  iteration 5 estimate
  final iteration estimate

 .goparameters   -- a dictionary of gauge-optimization parameter dictionaries:
 ---------------------------------------------------------
  




In [65]:
custom_gst_estimate_final_model = custom_gst_estimate.models['final iteration estimate']
print(custom_gst_estimate_final_model)

rho0 = FullState with dimension 4
 0.71   0   0 0.71


Mdefault = UnconstrainedPOVM with effect vectors:
0: FullPOVMEffect with dimension 4
 0.71   0   0 0.71

1: FullPOVMEffect with dimension 4
 0.71   0   0-0.71



[] = 
FullArbitraryOp with shape (4, 4)
 1.00   0   0   0
   0 1.00   0   0
   0   0 1.00   0
   0   0   0 1.00


Gxpi2:0 = 
MyXPi2Operator with shape (4, 4)
 1.00   0   0   0
   0 0.95   0   0
   0   0 0.09-0.95
   0   0 0.95 0.09


Gypi2:0 = 
FullArbitraryOp with shape (4, 4)
 1.00   0   0   0
   0   0   0 1.00
   0   0 1.00   0
   0-1.00   0   0






## How did we do?

In [66]:
estimated_parameter_vector = custom_gst_estimate_final_model['Gxpi2',0].to_vector()
actual_parameter_vector = customX_noisy_model['Gxpi2',0].to_vector()
print(f'Actual depolarization: {actual_parameter_vector[0]}')
print(f'Estimated depolarization: {estimated_parameter_vector[0]}')
print()
print(f'Actual over-rotation: {actual_parameter_vector[1]}')
print(f'Estimated over-rotation: {estimated_parameter_vector[1]}')

Actual depolarization: 0.05
Estimated depolarization: 0.05027056468448072

Actual over-rotation: 0.1
Estimated over-rotation: 0.09946312293095359
